
<table width="100%" style="padding:0; margin-left:-6px;">
    <tr style="padding=0;" width="100%">
        <td width="auto">
           <hr style="border:2px solid darkblue">
            <h1> nb3. Query objects by proposal id or bibliography code</h1>
           <hr style="border:2px solid darkblue">
        </td>
        <td width="60px">
           <img src="ALMAsmall.png" align="right"/> 
        </td>
    </tr>
</table>    
        

The relevant columns in the ALMA TAP service are 
* *proposal_id*
* *obs_publisher_did* 
* *bib_reference*
* *member_ous_uid*
--------- ----- -----



We first import the required modules, and link to the TAP service.

In [1]:
import numpy as np
import pyvo
import pandas as pd
pd.set_option('display.max_columns', None)

service = pyvo.dal.TAPService("https://almascience.eso.org/tap")      # for the EU ALMA TAP service

# service = pyvo.dal.TAPService("https://almascience.nao.ac.jp/tap")  # for the EA ALMA TAP service
# service = pyvo.dal.TAPService("https://almascience.nrao.edu/tap")   # for the NA ALMA TAP service

<hr style="border:2px solid darkblue"> </hr>

## Query a proposal ID

<hr style="border:2px solid darkblue"> </hr>

This function queries ALMA proposal IDs, also called project codes.


In [2]:
def query_proposal_id(service, proposal_id):
    """Queries for an ALMA project code
    
       service         pyvo TAPService instance
       proposal_id     ALMA proposal id in the form "2012.1.00123.S" or in the form "ADS/JAO.ALMA#2012.1.00123.S"
       
       returns         pandas table
       """

    query = f""" 
            SELECT *  
            FROM ivoa.obscore  
            WHERE obs_publisher_did like '%{proposal_id}%' 
            """    
    
    return service.search(query).to_table().to_pandas()

<hr style="border:2px solid darkblue"> </hr>


## Query a bibliography code

<hr style="border:2px solid darkblue"> </hr>

This function queries (part of) BibCodes as given out by [NASA ADS](https://ui.adsabs.harvard.edu).


In [3]:
def query_bib_reference(service, bibcode):
    """Queries for ALMA observations that have been used in a particular observation
    
       service         pyvo TAPService instance
       bibcode         BibCode in the NASA ADS format, e.g. "2017ApJ...834..140R. ""
                       Also supports part of the BibCode, e.g. "Natur"
       
       returns         pandas table
    """
    
    query = f""" 
            SELECT *  
            FROM ivoa.obscore  
            WHERE bib_reference like '%{bibcode}%' 
            """

    return service.search(query).to_table().to_pandas()

<hr style="border:2px solid darkblue"> </hr>


## Query a Member OUS ID
<hr style="border:2px solid darkblue"> </hr>

This function queries Member Observation Unit Set (OUS) IDs. Member OUS correspond to an independent dataset.

In [4]:
def query_member_ous(service, member_ous_id):
    """Queries for an ALMA Member OUS dataset
    
       service         pyvo TAPService instance
       member_ous_id   ALMA Member OUS dataset ID in the form "uid://A001/X123/X456" 
                       or in the form "uid___A001_X123_X456"
                       
       returns         pandas table
    """                       
    
    query = f""" 
            SELECT * 
            FROM ivoa.obscore  
            WHERE member_ous_uid = '{member_ous_id.replace("___","://").replace("_","/")}'  
            """
    
    return service.search(query).to_table().to_pandas()

<hr style="border:2px solid darkblue"> </hr>

## Query a publication ID and a specific source
<hr style="border:2px solid darkblue"> </hr>


In [5]:
def query_proposal_id_and_alma_source_name(service, proposal_id, source_name):
    """queries for a an ALMA project code and also for an ALMA source name
    
       service         pyvo TAPService instance
       proposal_id     ALMA proposal id in the form "2012.1.00123.S" or 
                       in the form "ADS/JAO.ALMA#2012.1.00123.S"
       source_name     ALMA source name as given by the PI in the proposal                
       
       returns         pandas table
    """    
    
    query = f"""  
            SELECT  *  
            FROM ivoa.obscore  
            WHERE obs_publisher_did like '%{proposal_id}%' 
            AND target_name like '%{source_name}%'  
            """
    
    return service.search(query).to_table().to_pandas()

------------------------

## Example 3a: List all observations carried on under a proposal ID

In [6]:
output = query_proposal_id(service, '2016.1.01308.S')
output.head(5) ### showing only 5 rows

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  http://almascience.org/aq?member_ous_id=uid://...     text/html   

      proposal_id data_rights  gal_longitude  gal_latitude  \
0  2016.1.01308.S      Public      77.437948    -38.582458   
1  2016.1.01308.S      Public      77.437948    -38.582458   
2  2016.1.01308.S      Public      77.437948    -38.582458   
3  2016.1.01308.S      Public      77.437948    -38.582458   
4  2016.1.01308.S      Public      80.570801    -53.100330   

             obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2016.1.01308.S           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2016.1.01308.S           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2016.1.01308.S           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2016.1.01308.S           ALMA           JAO            ALMA   
4  ADS/JAO.ALMA#2016.1.01308.S           ALMA           JAO            ALMA   

                 obs_id dataproduct_type  calib_level     target_name  \
0  uid://A001/X879/X314             cube            2      J2232+1143   
1  uid://A001/X879/X314             cube            2      J2232+1143   
2  uid://A001/X879/X314             cube            2      J2232+1143   
3  uid://A001/X879/X314             cube            2      J2232+1143   
4  uid://A001/X879/X314             cube            2  ULASJ2315+0143   

         s_ra      s_dec     s_fov  \
0  338.151704  11.730807  0.015766   
1  338.151704  11.730807  0.015766   
2  338.151704  11.730807  0.015766   
3  338.151704  11.730807  0.015766   
4  348.984300   1.730694  0.015766   

                                            s_region  s_resolution  \
0  Polygon ICRS 338.151704 11.722924 338.150195 1...      0.576869   
1  Polygon ICRS 338.151704 11.722924 338.150195 1...      0.576869   
2  Polygon ICRS 338.151704 11.722924 338.150195 1...      0.576869   
3  Polygon ICRS 338.151704 11.722924 338.150195 1...      0.576869   
4  Polygon ICRS 348.984300 1.738577 348.985778 1....      0.576861   

          t_min         t_max  t_exptime  t_resolution    em_min    em_max  \
0  57699.019868  57895.462736     907.20        907.20  0.003058  0.003118   
1  57699.019868  57895.462736     907.20        907.20  0.003090  0.003150   
2  57699.019868  57895.462736     907.20        907.20  0.002725  0.002772   
3  57699.019868  57895.462736     907.20        907.20  0.002750  0.002798   
4  57699.019868  57895.486087    5866.56       5866.56  0.002750  0.002798   

    em_res_power pol_states                                o_ucd band_list  \
0  100396.011062    /XX/YY/  phot.flux.density;phys.polarization         3   
1   99372.311222    /XX/YY/  phot.flux.density;phys.polarization         3   
2  110760.976427    /XX/YY/  phot.flux.density;phys.polarization         3   
3  109737.271411    /XX/YY/  phot.flux.density;phys.polarization         3   
4  109737.271411    /XX/YY/  phot.flux.density;phys.polarization         3   

   em_resolution                                            authors  \
0     307.023917  Banerji, Manda; Jones, Gareth C.; Carniani, St...   
1     307.023917  Banerji, Manda; Jones, Gareth C.; Carniani, St...   
2     307.023917  Banerji, Manda; Jones, Gareth C.; Carniani, St...   
3     307.023917  Banerji, Manda; Jones, Gareth C.; Carniani, St...   
4     307.019722  Banerji, Manda; Jones, Gareth C.; Carniani, St...   

                                        pub_abstract  publication_year  \
0  We present an unprecedented view of the morpho...              2018   
1  We present an unprecedented view of the morpho...              2018   
2  We present an unprecedented view of the morpho...              2018   
3  We present an unprec

Which were the science targets in these observations?

In [7]:
np.unique(output[output['science_observation']=='T']['target_name'])

array(['ULASJ1234+0907', 'ULASJ2315+0143'], dtype=object)

Which were the calibrators used in these observations?

In [8]:
np.unique(output[output['science_observation']=='F']['target_name'])

array(['Ganymede', 'J1229+0203', 'J1238+0723', 'J1239+0730', 'J2232+1143',
       'J2320+0513', 'J2326+0112', 'Neptune'], dtype=object)

---------------------------------------------------

## Example 3b: Search for one specific source (J1229+0203, calibrator) in a list of proposal IDs
Query the ASDM UIDs associated with a specific source observed multiple times within different observation sets.

In [9]:
source_name = 'J1229+0203'

# List of data sets where this source might be included
proposal_id_list =['ADS/JAO.ALMA#2015.1.00129.S', 'ADS/JAO.ALMA#2015.1.00329.S', 'ADS/JAO.ALMA#2015.1.00587.S', 'ADS/JAO.ALMA#2015.1.01012.S', 'ADS/JAO.ALMA#2016.1.00972.S', 'ADS/JAO.ALMA#2016.1.01308.S']

uids = []
for proposal_id in proposal_id_list:
    output = query_proposal_id_and_alma_source_name(service, proposal_id, source_name)
    if len(output) > 0:
       print(f"source {source_name} found in {proposal_id}")
       print(f"Is a science observation? {output['science_observation'].values}")
       uids += list(np.unique(output['member_ous_uid']))       
    else:
       print(f"source {source_name} NOT found in {proposal_id}") 
        
print("List of member_ous_uid that contain the particular source name and that are part of the proposal id list:")
print(uids)    


source J1229+0203 NOT found in ADS/JAO.ALMA#2015.1.00129.S
source J1229+0203 found in ADS/JAO.ALMA#2015.1.00329.S
Is a science observation? ['F' 'F' 'F' 'F']
source J1229+0203 found in ADS/JAO.ALMA#2015.1.00587.S
Is a science observation? ['F' 'F' 'F' 'F' 'F' 'F' 'F' 'F']
source J1229+0203 found in ADS/JAO.ALMA#2015.1.01012.S
Is a science observation? ['F' 'F' 'F' 'F']
source J1229+0203 found in ADS/JAO.ALMA#2016.1.00972.S
Is a science observation? ['F' 'F' 'F' 'F' 'F' 'F' 'F' 'F' 'F' 'F' 'F' 'F']
source J1229+0203 found in ADS/JAO.ALMA#2016.1.01308.S
Is a science observation? ['F' 'F' 'F' 'F' 'F' 'F' 'F' 'F']
List of member_ous_uid that contain the particular source name and that are part of the proposal id list:
['uid://A001/X2fe/Xbd5', 'uid://A001/X2fe/X80', 'uid://A001/X2fe/X82', 'uid://A001/X5a3/X83', 'uid://A001/X87d/X6d4', 'uid://A001/X899/X7e', 'uid://A001/X899/X82', 'uid://A001/X879/X318', 'uid://A001/X879/X31c']
